In [45]:
## Goal of this notebook is to figure out how to create and plots the outlines of the fields that have been plottted



# -- Take a shot at creating a plot of the entire fields.
# - take the kml file. create the centroid
# 	- create a merged polygon with complete outline of field
# 	- measure distance from centroid to the polygons (use 540 measurements for the outfield in current code. That would scale up to 2160 measurements.



## Dependencies and Setup
### Dependencies

from bs4 import BeautifulSoup
import pandas as pd
import numpy as np
import os
import re
import time
import matplotlib.pyplot as plt


In [46]:
### Going to bring the code in to start with a kml file and transform it into 
### a polygon that can be plotted.

## Open KML
## LOAD BLOCK###
#### Load data from kml file exported from Google Earth

file_path = ('TEMP/clean_tables/geo_data/all_high_schools.kml') # file path to kml file


# Read the KML file
with open(file_path) as file:
    xml_data = file.read()

# Initialize soup variables for parsing file
soup = BeautifulSoup(xml_data, 'xml')
folders = soup.Document.Folder
list = soup.Document.Folder.find_all('Folder')

# Create a list to store rows to append to the DataFrame
rows = []

# Loop through the folders and extract the data
for folder in list:
    try:
        field_name = folder.find('name').text
        foul = folder.find_all('coordinates')[0].text
        fop = folder.find_all('coordinates')[1].text
        notes = None

        # Check if there is a description tag, if so, use it for notes
        if folder.find('description') is not None:
            notes = folder.find('description').text

        row = {
            'field': field_name,
            'foul': foul,
            'fop': fop,
            'notes': notes
        }

        rows.append(row)

    except Exception as e:
        # Add name of folder to a list of failed folders
        failed.append(folder.find('name').text)
        print(f"Error processing folder: {folder.find('name').text}. Error message: {str(e)}")

# Convert the list of rows to a DataFrame
df = pd.DataFrame(rows, columns=['field', 'foul', 'fop', 'notes'])



In [47]:
# Clean the new dataframe


# Create a copy of the original DataFrame
df_cleaned = df.copy()

# Remove new line and space characters from coordinates
df_cleaned = df_cleaned.replace(r'\n','', regex=True) 
df_cleaned = df_cleaned.replace(r'\t','', regex=True) 

# Drop any duplicate rows
df_cleaned = df_cleaned.drop_duplicates(subset=['field'], keep='first')

# Drop any rows with empty fields
df_cleaned = df_cleaned[(df_cleaned != 0).all(1)]

##### Clean up polygon data and create a new home_plate column

def parse_coordinates(coord_string):
    coords = coord_string.split()
    parsed_coords = [tuple(map(float, coord.split(',')[:2])) for coord in coords]
    return parsed_coords

# Create a new column for the home_plate location using the first set of coordinates in the 'fop' column
df_cleaned['home_plate'] = df_cleaned['fop'].apply(lambda x: parse_coordinates(x)[0])

# Apply the parse_coordinates function to the 'foul' and 'fop' columns
df_cleaned['foul'] = df_cleaned['foul'].apply(parse_coordinates)
df_cleaned['fop'] = df_cleaned['fop'].apply(parse_coordinates)


############## AREA CALCULATION ##############


import pyproj
from shapely.geometry import Polygon
from shapely.ops import transform


def calculate_area(coords):
    # Create a Polygon object from the coordinates
    polygon = Polygon(coords)

    # Calculate the centroid of the polygon
    centroid = polygon.centroid

    # Create a custom LAEA projection centered on the centroid
    custom_projection = f"+proj=laea +lat_0={centroid.y} +lon_0={centroid.x} +x_0=0 +y_0=0 +datum=WGS84 +units=m +no_defs"

    # Create a transformer for converting coordinates to the custom LAEA projection
    transformer = pyproj.Transformer.from_crs(
        pyproj.CRS("EPSG:4326"),  # WGS 84 (latitude and longitude)
        pyproj.CRS(custom_projection),  # Custom LAEA projection
        always_xy=True
    )

    # Define a function to transform coordinates using the transformer
    def transform_coordinates(x, y):
        return transformer.transform(x, y)

    # Convert the coordinates to the custom LAEA projection
    polygon_laea = transform(transform_coordinates, polygon)

    # Calculate the area in square meters
    area_sqm = polygon_laea.area

    # Convert the area to square feet (1 square meter = 10.764 square feet)
    area_sqft = area_sqm * 10.764

    return area_sqft



### Call Function and add to dataframe
df_cleaned['foul_area_sqft'] = df_cleaned['foul'].apply(calculate_area)
df_cleaned['fop_area_sqft'] = df_cleaned['fop'].apply(calculate_area)

## Calculate the total area of the field and the ratio of foul area to field area
df_cleaned['field_area_sqft'] = df_cleaned['foul_area_sqft'] + df_cleaned['fop_area_sqft']
## Percentage foul area
df_cleaned['foul_area_per'] = df_cleaned['foul_area_sqft'] / df_cleaned['field_area_sqft']
## Fair to Foul Ratio
df_cleaned['fair_to_foul'] = df_cleaned['fop_area_sqft'] / df_cleaned['foul_area_sqft']




In [48]:
#### Orienting the map to the home plate location ####

### Find the center of the field
def calculate_centroid(coords):
    x_coords = [coord[0] for coord in coords]
    y_coords = [coord[1] for coord in coords]
    centroid_x = sum(x_coords) / len(coords)
    centroid_y = sum(y_coords) / len(coords)
    return (centroid_x, centroid_y)


## Find the bearing between the home plate and the center of the field
import math

def calculate_bearing(point1, point2):
    lat1, lon1 = math.radians(point1[1]), math.radians(point1[0])
    lat2, lon2 = math.radians(point2[1]), math.radians(point2[0])

    d_lon = lon2 - lon1

    x = math.cos(lat2) * math.sin(d_lon)
    y = math.cos(lat1) * math.sin(lat2) - math.sin(lat1) * math.cos(lat2) * math.cos(d_lon)

    bearing = math.degrees(math.atan2(x, y))
    bearing = (bearing + 360) % 360  # Normalize the bearing to the range [0, 360)

    return bearing

### Function to classify direction in laymans terms North, South, East, West, ect
def degrees_to_cardinal_direction(degrees):
    directions = ['N', 'NE', 'E', 'SE', 'S', 'SW', 'W', 'NW', 'N']
    index = round(degrees / 45)
    return directions[index]

In [49]:
# Calculate the centroid of the outfield fence coordinates for each row
df_cleaned['fop_centroid'] = df_cleaned['fop'].apply(lambda coords: calculate_centroid(coords[1:]))

# Calculate the bearing between home plate and the centroid for each row
df_cleaned['field_orientation'] = df_cleaned.apply(lambda row: calculate_bearing(row['home_plate'], row['fop_centroid']), axis=1)

# Convert the bearing to a cardinal direction
df_cleaned['field_cardinal_direction'] = df_cleaned['field_orientation'].apply(degrees_to_cardinal_direction)

# rename 'field' to 'park_name'
df_cleaned.rename(columns={'field': 'park_name'}, inplace=True)




In [50]:
## print one record from the fop column
print(df_cleaned['fop'][10])

[(-84.6479335, 43.3931241), (-84.6491713, 43.3931046), (-84.6491726, 43.3930539), (-84.649174, 43.3929964), (-84.649178, 43.392938), (-84.649174, 43.3928532), (-84.6491713, 43.3927879), (-84.6491686, 43.3927333), (-84.6491498, 43.3926671), (-84.6491217, 43.3926164), (-84.6490855, 43.3925618), (-84.6490399, 43.3925063), (-84.6489889, 43.3924536), (-84.6489366, 43.3924186), (-84.648891, 43.3923825), (-84.6488172, 43.3923338), (-84.6487314, 43.3922997), (-84.6486617, 43.3922685), (-84.648604, 43.3922519), (-84.6485329, 43.3922353), (-84.6484766, 43.3922334), (-84.6483948, 43.3922285), (-84.6482969, 43.3922275), (-84.6481816, 43.3922285), (-84.6480542, 43.3922285), (-84.6478812, 43.3922266), (-84.6479335, 43.3931241)]


In [51]:
### Create the merged polygon from the foul and fop coordinates
## Save the merged polygon into a new column called 'full_polygon'

from shapely.geometry import Polygon
from shapely.ops import cascaded_union
from shapely.ops import unary_union

# Assuming df_cleaned is your dataframe, and 'fop' and 'foul' are your columns

# Convert list of coordinate tuples to Shapely Polygon objects
df_cleaned['fop'] = df_cleaned['fop'].apply(lambda x: Polygon(x))
df_cleaned['foul'] = df_cleaned['foul'].apply(lambda x: Polygon(x))

# Function to merge polygons
def merge_polygons(row):
    return unary_union([row['fop'], row['foul']])

# Create new column with merged polygons
df_cleaned['merged'] = df_cleaned.apply(merge_polygons, axis=1)



c:\Users\Justin\anaconda3\lib\site-packages\pandas\core\dtypes\cast.py:1981: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  result[:] = values


In [52]:
df_cleaned.sample(5)

park_name  \
380              Pinckney HS - Field 2   
317  Middleville Thornapple Kellogg HS   
3                            Adrian HS   
497    Ypsilanti - Lincoln High School   
488                     White Cloud HS   

                                                  foul  \
380  POLYGON ((-83.9286677 42.4494733, -83.9287173 ...   
317  POLYGON ((-85.4907235 42.7094929, -85.4913793 ...   
3    POLYGON ((-84.0416584 41.9091676, -84.0416691 ...   
497  POLYGON ((-83.6146339 42.1610319, -83.6154399 ...   
488  POLYGON ((-85.7764106 43.560252, -85.776428 43...   

                                                   fop notes  \
380  POLYGON ((-83.9286677 42.4494733, -83.9274795 ...  None   
317  POLYGON ((-85.4907235 42.7094929, -85.4897244 ...  None   
3    POLYGON ((-84.0416584 41.9091676, -84.0405493 ...  None   
497  POLYGON ((-83.6146339 42.1610319, -83.6138159 ...  None   
488  POLYGON ((-85.7764106 43.560252, -85.7752103 4...  None   

                    home_plate  foul_area_sqft  fop_area_sqft  \
380  (-83.9286677, 42.4494733)    23445.527643   89406.690924   
317  (-85.4907235, 42.7094929)    37662.003536  100468.057374   
3    (-84.0416584, 41.9091676)    36619.533089   86478.745151   
497  (-83.6146339, 42.1610319)    26750.368616   92731.755753   
488   (-85.7764106, 43.560252)    29715.248930   84539.030064   

     field_area_sqft  foul_area_per  fair_to_foul  \
380    112852.218568       0.207754      3.813379   
317    138130.060910       0.272656      2.667624   
3      123098.278240       0.297482      2.361547   
497    119482.124368       0.223886      3.466560   
488    114254.278994       0.260080      2.844971   

                                 fop_centroid  field_orientation  \
380    (-83.9279219035714, 42.45006191071428)          43.073175   
317   (-85.49045522142858, 42.71031763928572)          13.442617   
3    (-84.04087369166668, 41.909742770833326)          45.435207   
497  (-83.61459238148151, 42.161839648148145)           2.181947   
488  (-85.77567388666665, 43.560796399999994)          44.439535   

    field_cardinal_direction  \
380                       NE   
317                        N   
3                         NE   
497                        N   
488                       NE   

                                                merged  
380  POLYGON ((-83.9274822 42.4494605, -83.9282976 ...  
317  POLYGON ((-85.4899698 42.7096644, -85.4906136 ...  
3    POLYGON ((-84.0405547 41.9091536, -84.0408055 ...  
497  POLYGON ((-83.6137971 42.1615946, -83.614076 4...  
488  POLYGON ((-85.7751754 43.5600829, -85.7765192 ...

In [53]:
############# FENCE DISTANCE CALCULATION #############

from geopy.distance import great_circle
import numpy as np
from shapely.geometry import MultiPolygon





def interpolate_points(start, end, length_ratio):
    start_np = np.array(start)
    end_np = np.array(end)
    return tuple(start_np + (end_np - start_np) * length_ratio)

def calculate_distances(home_plate, coords, num_points=2160):
    distances = []

    def is_same_point(point1, point2, tolerance=1e-6):
        return abs(point1[0] - point2[0]) < tolerance and abs(point1[1] - point2[1]) < tolerance
    
    home_plate_lat_lon = (home_plate[1], home_plate[0])
    distances = []

    # Calculate total line length
    total_length = 0
    segments = []
    for i in range(len(coords) - 1):
        start = coords[i]
        end = coords[i + 1]
        if not is_same_point(home_plate, start) and not is_same_point(home_plate, end):
            segment_length = great_circle((start[1], start[0]), (end[1], end[0])).feet
            segments.append((start, end, segment_length))
            total_length += segment_length

    # Calculate the distance between equally spaced points
    spacing = total_length / (num_points - 1)

    # Interpolate points and calculate distances
    current_length = 0
    segment_index = 0
    for i in range(num_points):
        while segment_index < len(segments) - 1 and current_length > segments[segment_index][2]:
            current_length -= segments[segment_index][2]
            segment_index += 1

        start, end, segment_length = segments[segment_index]
        length_ratio = current_length / segment_length
        point = interpolate_points(start, end, length_ratio)
        distance = great_circle(home_plate_lat_lon, (point[1], point[0])).feet
        distances.append(distance)

        current_length += spacing

    return distances




df_cleaned['distances'] = df_cleaned.apply(
    lambda row: calculate_distances(
        row['home_plate'], 
        row['merged'].exterior.coords[:]
    ) if not isinstance(row['merged'], MultiPolygon) else np.nan, 
    axis=1
)




# # Calculate max, min, and average distances for each row
# df_cleaned['max_distance'] = df_cleaned['distances'].apply(max)
# df_cleaned['min_distance'] = df_cleaned['distances'].apply(min)
# df_cleaned['avg_distance'] = df_cleaned['distances'].apply(lambda distances: sum(distances) / len(distances))
# # get the median distance
# df_cleaned['median_distance'] = df_cleaned['distances'].apply(lambda distances: np.median(distances))


In [54]:
## Show the resulting dataframe

# df_cleaned.head(10)



In [55]:
import matplotlib.pyplot as plt

# Plot the distances and their mirrored version for the first 5 rows
for i in range(25):
    try:
        distances = df_cleaned['distances'][i]
        half = len(distances) // 2  # Find the middle index
        distances_half_1 = distances[:half]  # First half of the distances
        distances_half_2 = distances[half:][::-1]  # Second half of the distances, reversed
        
        plt.plot([i for i in range(half)], distances_half_1, label=df_cleaned['park_name'][i] + '_1')
        plt.plot([i for i in range(half)], distances_half_2, label=df_cleaned['park_name'][i] + '_2')
    except Exception as e:
        pass


# set the size of the plot
plt.rcParams["figure.figsize"] = (20,15)
plt.xlim(-100, 1200)

# Set the image resolution
plt.rcParams['figure.dpi'] = 600

ax = plt.gca()
ax.set_aspect(2.5)

plt.xlabel("Index")
plt.ylabel("Distance (feet)")


# plt.legend()
plt.show()


In [56]:
### make a plot of a couple of the fences using the distance column

import matplotlib.pyplot as plt

# Plot the distances for the first 5 rows
for i in range(5):
    plt.plot(df_cleaned['distances'][i])
plt.show()


In [57]:
############## NEW CODE FOR NEW FIELD VISUALIZATIONS ##############

## create plots with the same format as the NCAA site ones with high school data

### apply school colors to the plots from the MHSAA data 
## should be easy to merge on closest field
## should be able to slice by conference, class ect pretty easily

In [58]:
df_cleaned.columns

Index(['park_name', 'foul', 'fop', 'notes', 'home_plate', 'foul_area_sqft',
       'fop_area_sqft', 'field_area_sqft', 'foul_area_per', 'fair_to_foul',
       'fop_centroid', 'field_orientation', 'field_cardinal_direction',
       'merged', 'distances'],
      dtype='object')

In [59]:
df = df_cleaned.copy()


### look at the data
# print a report of the number of fields and some basic stats
print('Number of fields: ', len(df))



Number of fields:  494


In [60]:
## open MHSAA Data

path = 'data\MHSAA\MHSAA_School_Data_with_Fields.csv'

school_df = pd.read_csv(path)

In [61]:
## school_df.head()
school_df.columns

Index(['SchoolId', 'SportId', 'PopularName', 'ProperName', 'NickName',
       'Colors', 'LeaugeName', 'LeaugeId', 'HeadCoach', 'PrimaryColorCode',
       'ImagePath', 'Classification', 'Record', 'Enrollment', 'City', 'State',
       'Address1', 'Address2', 'Zip', 'Phone', 'Fax', 'VanityUrl', 'MapURL',
       'WebSite', 'IsMiddleSchool', 'ClassificationCalculationSteps',
       'ClassificationCalculationStepsHtml', 'SportSeasonId', 'EnrollmentData',
       'TicketUrl', 'OldSchoolId', 'SchoolNameWithId', 'Lat', 'Lng',
       'Closest_Field_1', 'Closest_Field_2', 'Closest_Field_3', 'Distance_1',
       'Distance_2', 'Distance_3', 'Enrollment_Class',
       'Enrollment_Class_Calculated'],
      dtype='object')

In [62]:
# merge on Closest_Field_1

df = df.merge(school_df, left_on='park_name', right_on='Closest_Field_1', how='left')

df.columns

Index(['park_name', 'foul', 'fop', 'notes', 'home_plate', 'foul_area_sqft',
       'fop_area_sqft', 'field_area_sqft', 'foul_area_per', 'fair_to_foul',
       'fop_centroid', 'field_orientation', 'field_cardinal_direction',
       'merged', 'distances', 'SchoolId', 'SportId', 'PopularName',
       'ProperName', 'NickName', 'Colors', 'LeaugeName', 'LeaugeId',
       'HeadCoach', 'PrimaryColorCode', 'ImagePath', 'Classification',
       'Record', 'Enrollment', 'City', 'State', 'Address1', 'Address2', 'Zip',
       'Phone', 'Fax', 'VanityUrl', 'MapURL', 'WebSite', 'IsMiddleSchool',
       'ClassificationCalculationSteps', 'ClassificationCalculationStepsHtml',
       'SportSeasonId', 'EnrollmentData', 'TicketUrl', 'OldSchoolId',
       'SchoolNameWithId', 'Lat', 'Lng', 'Closest_Field_1', 'Closest_Field_2',
       'Closest_Field_3', 'Distance_1', 'Distance_2', 'Distance_3',
       'Enrollment_Class', 'Enrollment_Class_Calculated'],
      dtype='object')

In [63]:
## se null values
df.isnull().sum()


park_name                               0
foul                                    0
fop                                     0
notes                                 869
home_plate                              0
foul_area_sqft                          0
fop_area_sqft                           0
field_area_sqft                         0
foul_area_per                           0
fair_to_foul                            0
fop_centroid                            0
field_orientation                       0
field_cardinal_direction                0
merged                                  0
distances                              12
SchoolId                               35
SportId                                35
PopularName                            35
ProperName                             35
NickName                              123
Colors                                113
LeaugeName                            309
LeaugeId                               35
HeadCoach                         

In [64]:
## drop teams with no classification
df = df.dropna(subset=['Classification'])

## Drop teams with nothing in the distances column
df = df.dropna(subset=['distances'])

# show counts of each classification
df['Classification'].value_counts()

## SHow the variation in distance_1 distance_2 and distance_3

df['Distance_1'].describe()
# drop extream values
df = df[df['Distance_1'] < 500]
df['Distance_1'].describe()

# show histogram of distance_1
df['Distance_1'].hist(bins=20)

## drop any outside 2 standard deviations
df = df[df['Distance_1'] < df['Distance_1'].mean() + 2*df['Distance_1'].std()]
df['Distance_1'].describe()

## show the distribution of distance_1
df['Distance_1'].hist(bins=20)



<AxesSubplot:>

In [65]:
## DATAFRAME STATS, LENGTH, AND CLASSIFICATION

## show the number of fields in each classification
df['Classification'].value_counts()

## show nulls
df.isnull().sum()

## drop any without league name
df = df.dropna(subset=['LeaugeName'])

## show the number of fields in each classification
df['Classification'].value_counts()


A    167
B    162
C    145
D     99
Name: Classification, dtype: int64

In [66]:
## Create a dataframe for each classification
df_a = df[df['Classification'] == 'A']
df_b = df[df['Classification'] == 'B']
df_c = df[df['Classification'] == 'C']
df_d = df[df['Classification'] == 'D']



In [67]:
## Check the distances columns for each classification
# List of dfs
dfs = [df_a, df_b, df_c, df_d]

# ## get the mean distance for each classification
# for df in dfs:
#     print(df['distances'].mean())



# Check for null rows in distances

for df in dfs:
    print(df['distances'].isnull().sum())







0
0
0
0


In [68]:
def get_min_max_mean_fence_distances(df):
    ## create the min max and mean fence distance rows
    # Transpose the dataframe to get the 
    transposed_df = pd.DataFrame(df['distances'].to_list()).transpose()

    # Calculate min, max, mean, median, Q1 and Q3 for each row
    min_fence_distances = transposed_df.min(axis=1)
    max_fence_distances = transposed_df.max(axis=1)
    mean_fence_distances = transposed_df.mean(axis=1)
    median_fence_distances = transposed_df.median(axis=1)
    ## create profiles for standard deviation
    std_fence_distances = transposed_df.std(axis=1)
    first_fence_distances = mean_fence_distances + std_fence_distances
    third_fence_distances = mean_fence_distances - std_fence_distances

    # Create a new DataFrame to store these values
    new_df = pd.DataFrame({
        'park_name': ['Min', 'Max', 'Mean', 'Median', 'Q1', 'Q3'],
        'distances': [
            min_fence_distances.tolist(), 
            max_fence_distances.tolist(),
            mean_fence_distances.tolist(),
            median_fence_distances.tolist(), # Add a comma here
            first_fence_distances.tolist(),
            third_fence_distances.tolist()
        ]
    })

    # For all other columns in the original DataFrame, add a column of NaN values in the new DataFrame
    for column in df.columns:
        if column not in new_df.columns:
            new_df[column] = np.nan

    # Concatenate the new DataFrame with the original one
    df = pd.concat([df, new_df], ignore_index=True)

In [69]:
## Run the function for each classification

list_of_dfs = [df_a, df_b, df_c, df_d]

for df in list_of_dfs:
    get_min_max_mean_fence_distances(df)


### 
    

In [81]:

## Look at each dataframe
df_a.head()
# df_b.head()
# df_c.head()
# df_d.tail()


park_name  \
2   Adams Butzel Complex - Detroit Communication M...   
5   Adams Butzel Complex - Detroit Communication M...   
10                                          Adrian HS   
14                                Algonac High School   
16                                         Allegan HS   

                                                 foul  \
2   POLYGON ((-83.1678186 42.3966942, -83.1678776 ...   
5   POLYGON ((-83.1678186 42.3966942, -83.1678776 ...   
10  POLYGON ((-84.0416584 41.9091676, -84.0416691 ...   
14  POLYGON ((-82.5823976 42.6286202, -82.5813154 ...   
16  POLYGON ((-85.8755219 42.5312676, -85.8754455 ...   

                                                  fop notes  \
2   POLYGON ((-83.1678186 42.3966942, -83.1665385 ...  None   
5   POLYGON ((-83.1678186 42.3966942, -83.1665385 ...  None   
10  POLYGON ((-84.0416584 41.9091676, -84.0405493 ...  None   
14  POLYGON ((-82.5823976 42.6286202, -82.5826256 ...  None   
16  POLYGON ((-85.8755219 42.5312676, -85.8765814 ...  None   

                   home_plate  foul_area_sqft  fop_area_sqft  field_area_sqft  \
2   (-83.1678186, 42.3966942)    43132.874486   94900.435141    138033.309627   
5   (-83.1678186, 42.3966942)    43132.874486   94900.435141    138033.309627   
10  (-84.0416584, 41.9091676)    36619.533089   86478.745151    123098.278240   
14  (-82.5823976, 42.6286202)    30409.852869   83315.423957    113725.276826   
16  (-85.8755219, 42.5312676)    35265.755123   82903.009176    118168.764299   

    foul_area_per  fair_to_foul  ...        Lat        Lng  \
2        0.312482      2.200188  ...  42.332797 -83.118864   
5        0.312482      2.200188  ...  42.360772 -83.221367   
10       0.297482      2.361547  ...  41.909697 -84.045983   
14       0.267397      2.739751  ...  42.627608 -82.582650   
16       0.298436      2.350808  ...  42.529840 -85.873250   

                                      Closest_Field_1  \
2   Adams Butzel Complex - Detroit Communication M...   
5   Adams Butzel Complex - Detroit Communication M...   
10                                          Adrian HS   
14                                Algonac High School   
16                                         Allegan HS   

                Closest_Field_2                       Closest_Field_3  \
2                 Melvindale HS         Detroit Martin Luther King HS   
5           Redford Thurston HS                           Dearborn HS   
10  Adrian Lenawee Christian HS  Ann Arbor Greenhills HS? - Practice?   
14               Marine City HS            New Haven HS - high school   
16                   Hopkins HS                             Otsego HS   

    Distance_1  Distance_2 Distance_3 Enrollment_Class  \
2     5.073164    5.171068   5.437861            Div_2   
5     3.691918    4.372884   4.375828            Div_2   
10    0.225348    1.942878   3.371869            Div_1   
14    0.071103    7.103062  12.487290            Div_2   
16    0.152009    8.671278   9.475276            Div_2   

   Enrollment_Class_Calculated  
2                            C  
5                            C  
10                           D  
14                           C  
16                           C  

[5 rows x 57 columns]

In [70]:
## Validate the color values used in the plot

import matplotlib.colors as mcolors


def validate_color(color, default='white'):
    # Check if color is NaN (which is of float type), if yes, return default color
    if pd.isnull(color):
        return default

    # Strip non-breaking spaces and other leading/trailing whitespace
    color = color.strip()
    
    # Check if color is a valid hex color code
    if re.match('^#[0-9a-fA-F]{6}$', color):
        return color
    
    # Check if color is a valid matplotlib color name
    if color in mcolors.CSS4_COLORS:
        return color

    # If color is not valid, return the default color
    return default

In [ ]:
########### USE CODE BELOW TO CREATE THE PLOTS ##############

### NEED TO REFACTOR AND SIMPLIFY FOR HS SLICES AND DATA FORMAT

In [71]:





def plot_distances(df, row_index):
    # Get rows with 'Min', 'Max', 'Mean', 'Q1', 'Q3' in 'park_name'
    rows_to_plot = df[df['park_name'].isin(['Min', 'Max', 'Mean', 'Q1', 'Q3'])]
    
    # Get the row to be highlighted
    highlighted_row = df.loc[row_index]
    
    # Create a new figure
    fig = plt.figure(figsize=(10,8))
    fig.patch.set_facecolor('black')
    


    # Apply the validate_color function to the color2 column
    df['color2'] = df['color2'].apply(validate_color)
    
    
    # Loop over these rows and plot a line graph for each
    for index, row in rows_to_plot.iterrows():
        if row['park_name'] in ['Q1', 'Q3']: # If Q1 or Q3, plot thinner, dotted line
            plt.plot(row['distances'], linestyle='dotted', alpha=0.3, color='grey', label=row['park_name'])
        else:
            plt.plot(row['distances'], linestyle='dashed', alpha=0.5, label=row['park_name'])

        # Add text labels for Min, Max and Mean lines
        if row['park_name'] in ['Min', 'Max', 'Mean']:
            plt.text(len(row['distances'])-1, row['distances'][-1], row['park_name'], color='blue', va='center')

        ## Shade the standard green below the Min Line
        # Check if the current row is 'Min', if so, add shading
        if row['park_name'] == 'Min':
            plt.fill_between(range(len(row['distances'])), plt.ylim()[0], row['distances'], color='green', alpha=0.4)

        # # SHADES IN TEAM COLOR BELOW MIN LINE
        # if row['park_name'] == 'Min' and pd.notnull(highlighted_row['color1']):
        #     plt.fill_between(range(len(row['distances'])), row['distances'], color=highlighted_row['color1'], alpha=0.4)

        # Check if the current row is 'Max', if so, add shading
        if row['park_name'] == 'Max':
            plt.fill_between(range(len(row['distances'])), row['distances'], color='yellow', alpha=0.2)

        ## SHADE IN USING TEAM COLORS ABOVE MAX LINE
        if row['park_name'] == 'Max' and pd.notnull(highlighted_row['color1']):
            plt.fill_between(range(len(row['distances'])), plt.ylim()[1], row['distances'], color=highlighted_row['color1'], alpha=1.0)

            
    # Plot the highlighted row with a thicker line
    plt.plot(highlighted_row['distances'], linewidth=2, label=highlighted_row['park_name'])

    
    
    # Set the minimum and maximum values of y-axis
    plt.ylim([300, 420])

    # set the font for all the labels
    plt.rcParams['font.family'] = 'sans-serif'

    # Change y-axis labels and tick marks to be white
    plt.ylabel('Distance (feet)', color='white', size=14)
    plt.tick_params(axis='y', colors='white', size=12)



    # Hide x axis ticks
    plt.xticks([])



    # Add a main title and subtitle with the field name and host school
    plt.suptitle(f"{highlighted_row['display_name']}", color='black', fontsize=20, y=.25)
    plt.title(f"({highlighted_row['host_school']})", color='black', fontsize=16, y=.05)

    # Add text with statistics for each field
    home_runs = highlighted_row['home_runs']
    if not np.isnan(home_runs):
        plt.annotate(f"Home Runs: {round(home_runs)}", xy=(0.05, 0.90), xycoords='axes fraction', color=validate_color(highlighted_row['color2']), fontsize=20, weight='bold', ha="left", va="bottom")

    HR_G_rank = highlighted_row['HR_G_rank']
    if not np.isnan(HR_G_rank):
        plt.annotate(f"Rank: {round(HR_G_rank)}", xy=(0.65, 0.85), xycoords='axes fraction', color=validate_color(highlighted_row['color2']), fontsize=20,  ha="left", va="bottom")

    games = highlighted_row['games']
    if not np.isnan(games):
        plt.annotate(f"Games: {round(games)}", xy=(0.05, 0.85), xycoords='axes fraction', color=validate_color(highlighted_row['color2']), fontsize=16, ha="left", va="bottom")
    if not np.isnan(highlighted_row['home_runs_per_game']):
        plt.annotate(f"HR / G: {highlighted_row['home_runs_per_game']}", xy=(0.65, 0.90), xycoords='axes fraction', color=validate_color(highlighted_row['color2']), fontsize=20, weight='bold', ha="left", va="bottom")


    
    #Games: {highlighted_row['games']} HR / G: {highlighted_row['home_runs_per_game']} ", xy=(0.05, 0.95), xycoords='axes fraction', color="white", fontsize=16, ha="left", va="bottom")


    

    
    

    # Reverse the x-axis
    plt.gca().invert_xaxis()

    # Generate the file path
    file_path = os.path.join(output_dir, f"{highlighted_row['HR_G_rank']}_{highlighted_row['host_school']}.png")
    
    # Save the figure
    plt.savefig(file_path, transparent=False)


    # Close the figure to free up memory
    plt.close()

    # Return the file path
    return file_path

# Add a new column 'file_path' to the DataFrame to store the file paths
# df['file_path'] = [plot_distances(df, i) for i in df.index]

In [72]:
df.columns

Index(['park_name', 'foul', 'fop', 'notes', 'home_plate', 'foul_area_sqft',
       'fop_area_sqft', 'field_area_sqft', 'foul_area_per', 'fair_to_foul',
       'fop_centroid', 'field_orientation', 'field_cardinal_direction',
       'merged', 'distances', 'SchoolId', 'SportId', 'PopularName',
       'ProperName', 'NickName', 'Colors', 'LeaugeName', 'LeaugeId',
       'HeadCoach', 'PrimaryColorCode', 'ImagePath', 'Classification',
       'Record', 'Enrollment', 'City', 'State', 'Address1', 'Address2', 'Zip',
       'Phone', 'Fax', 'VanityUrl', 'MapURL', 'WebSite', 'IsMiddleSchool',
       'ClassificationCalculationSteps', 'ClassificationCalculationStepsHtml',
       'SportSeasonId', 'EnrollmentData', 'TicketUrl', 'OldSchoolId',
       'SchoolNameWithId', 'Lat', 'Lng', 'Closest_Field_1', 'Closest_Field_2',
       'Closest_Field_3', 'Distance_1', 'Distance_2', 'Distance_3',
       'Enrollment_Class', 'Enrollment_Class_Calculated'],
      dtype='object')

In [ ]:
### Run the plot function over each dataframe 
df['file_path'] = [plot_distances(df, i) for i in df.index]



In [73]:
## Show the count of league information
df['LeaugeName'].value_counts()

Southern Central Athletic Association    14
North Central Thumb League               10
North Star League                         8
West Michigan 'D' League                  7
Copper Mountain Conference                6
Michigan Independent Ath Conf             6
Catholic High School League               6
Mid-State Activities Conference           5
Northwest Conference                      5
Eastern UP Athletic Conference            4
Alliance League                           4
Detroit Public Schools League             4
Northern Lights League                    3
Detroit Metro Athletic Conference         3
Charter School Conference                 3
Southwest 10 Conference                   2
Michigan Metro Athletic Conference        1
Skyline Central Conference                1
BCS League                                1
Crossroads Athletic Conference            1
Southwestern Athletic Conference          1
Straits Area Conference                   1
Genesee Area Conference         

In [74]:
## 

In [75]:
############ STARTING HERE ###########

# create some graphics like the ones for the ncaa fence

In [76]:
# import matplotlib.pyplot as plt
# import pandas as pd
# import numpy as np

# def plot_field(df):
#     # generate an array of angles for plotting
#     angles = np.linspace(0, 2 * np.pi, 2160, endpoint=False)

#     for idx, row in df.iterrows():
#         # adjusting the angles based on field orientation
#         adjusted_angles = (angles + np.deg2rad(row['field_orientation'])) % (2*np.pi)
        
#         # convert polar coordinates to cartesian coordinates
#         x = row['fop_centroid'][0] + np.array(row['distances']) * np.cos(adjusted_angles)
#         y = row['fop_centroid'][1] + np.array(row['distances']) * np.sin(adjusted_angles)
        
#         plt.figure()
#         plt.plot(x, y)
#         plt.title(row['park_name'])
#         plt.xlabel("Feet")
#         plt.ylabel("Feet")
#         plt.gca().set_aspect('equal', adjustable='box')
#         plt.show()

# # Let's assume you have a DataFrame df
# # df = pd.read_csv('your_data.csv')  # replace with your actual data file
# plot_field(df_cleaned)
